# Part 2 of 3
## Data Preparation

HDB resale data is being used for this exercise. It is obtained from Data.gov ([source](https://data.gov.sg/dataset/resale-flat-prices)) There are a total of 5 csv files extracted and will be merged together. 

The two additional coordinations taken into account are distances from resale flats to shopping malls and MRT stations. In order to calculate that, coordinates are obtained using Onemap api. 

The bulk of data visualisations are done on Tableau after the data has been cleaned and finalised. ([Tableau link](https://public.tableau.com/app/profile/desmond.yap/viz/HDBResale_16789477762870/HDBResalePriceAnalysis?publish=yes))

In [1]:
import pandas as pd
import requests
from requests.exceptions import Timeout
import re
from datetime import datetime

In [2]:
resale_19901999_df = pd.read_csv('data/1990to1999.csv')
resale_19901999_df.head()

month        town flat_type block       street_name storey_range  \
0  1990-01  ANG MO KIO    1 ROOM   309  ANG MO KIO AVE 1     10 TO 12   
1  1990-01  ANG MO KIO    1 ROOM   309  ANG MO KIO AVE 1     04 TO 06   
2  1990-01  ANG MO KIO    1 ROOM   309  ANG MO KIO AVE 1     10 TO 12   
3  1990-01  ANG MO KIO    1 ROOM   309  ANG MO KIO AVE 1     07 TO 09   
4  1990-01  ANG MO KIO    3 ROOM   216  ANG MO KIO AVE 1     04 TO 06   

   floor_area_sqm      flat_model  lease_commence_date  resale_price  
0            31.0        IMPROVED                 1977          9000  
1            31.0        IMPROVED                 1977          6000  
2            31.0        IMPROVED                 1977          8000  
3            31.0        IMPROVED                 1977          6000  
4            73.0  NEW GENERATION                 1976         47200

In [3]:
resale_19901999_df.info()
resale_19901999_df.shape

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 287196 entries, 0 to 287195
Data columns (total 10 columns):
 #   Column               Non-Null Count   Dtype  
---  ------               --------------   -----  
 0   month                287196 non-null  object 
 1   town                 287196 non-null  object 
 2   flat_type            287196 non-null  object 
 3   block                287196 non-null  object 
 4   street_name          287196 non-null  object 
 5   storey_range         287196 non-null  object 
 6   floor_area_sqm       287196 non-null  float64
 7   flat_model           287196 non-null  object 
 8   lease_commence_date  287196 non-null  int64  
 9   resale_price         287196 non-null  int64  
dtypes: float64(1), int64(2), object(7)
memory usage: 21.9+ MB


(287196, 10)

In [4]:
resale_20002012_df = pd.read_csv('data/2000to2012.csv')
resale_20002012_df.head()

month        town flat_type block       street_name storey_range  \
0  2000-01  ANG MO KIO    3 ROOM   170  ANG MO KIO AVE 4     07 TO 09   
1  2000-01  ANG MO KIO    3 ROOM   174  ANG MO KIO AVE 4     04 TO 06   
2  2000-01  ANG MO KIO    3 ROOM   216  ANG MO KIO AVE 1     07 TO 09   
3  2000-01  ANG MO KIO    3 ROOM   215  ANG MO KIO AVE 1     07 TO 09   
4  2000-01  ANG MO KIO    3 ROOM   218  ANG MO KIO AVE 1     07 TO 09   

   floor_area_sqm      flat_model  lease_commence_date  resale_price  
0            69.0        Improved                 1986      147000.0  
1            61.0        Improved                 1986      144000.0  
2            73.0  New Generation                 1976      159000.0  
3            73.0  New Generation                 1976      167000.0  
4            67.0  New Generation                 1976      163000.0

In [5]:
resale_20002012_df.info()
resale_20002012_df.shape

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 369651 entries, 0 to 369650
Data columns (total 10 columns):
 #   Column               Non-Null Count   Dtype  
---  ------               --------------   -----  
 0   month                369651 non-null  object 
 1   town                 369651 non-null  object 
 2   flat_type            369651 non-null  object 
 3   block                369651 non-null  object 
 4   street_name          369651 non-null  object 
 5   storey_range         369651 non-null  object 
 6   floor_area_sqm       369651 non-null  float64
 7   flat_model           369651 non-null  object 
 8   lease_commence_date  369651 non-null  int64  
 9   resale_price         369651 non-null  float64
dtypes: float64(2), int64(1), object(7)
memory usage: 28.2+ MB


(369651, 10)

In [6]:
resale_20122014_df = pd.read_csv('data/2012to2014.csv')
resale_20122014_df.head()

month        town flat_type block        street_name storey_range  \
0  2012-03  ANG MO KIO    2 ROOM   172   ANG MO KIO AVE 4     06 TO 10   
1  2012-03  ANG MO KIO    2 ROOM   510   ANG MO KIO AVE 8     01 TO 05   
2  2012-03  ANG MO KIO    3 ROOM   610   ANG MO KIO AVE 4     06 TO 10   
3  2012-03  ANG MO KIO    3 ROOM   474  ANG MO KIO AVE 10     01 TO 05   
4  2012-03  ANG MO KIO    3 ROOM   604   ANG MO KIO AVE 5     06 TO 10   

   floor_area_sqm      flat_model  lease_commence_date  resale_price  
0            45.0        Improved                 1986      250000.0  
1            44.0        Improved                 1980      265000.0  
2            68.0  New Generation                 1980      315000.0  
3            67.0  New Generation                 1984      320000.0  
4            67.0  New Generation                 1980      321000.0

In [7]:
resale_20122014_df.info()
resale_20122014_df.shape

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 52203 entries, 0 to 52202
Data columns (total 10 columns):
 #   Column               Non-Null Count  Dtype  
---  ------               --------------  -----  
 0   month                52203 non-null  object 
 1   town                 52203 non-null  object 
 2   flat_type            52203 non-null  object 
 3   block                52203 non-null  object 
 4   street_name          52203 non-null  object 
 5   storey_range         52203 non-null  object 
 6   floor_area_sqm       52203 non-null  float64
 7   flat_model           52203 non-null  object 
 8   lease_commence_date  52203 non-null  int64  
 9   resale_price         52203 non-null  float64
dtypes: float64(2), int64(1), object(7)
memory usage: 4.0+ MB


(52203, 10)

In [8]:
resale_20152016_df = pd.read_csv('data/2015to2016.csv')
resale_20152016_df.head()

month        town flat_type block        street_name storey_range  \
0  2015-01  ANG MO KIO    3 ROOM   174   ANG MO KIO AVE 4     07 TO 09   
1  2015-01  ANG MO KIO    3 ROOM   541  ANG MO KIO AVE 10     01 TO 03   
2  2015-01  ANG MO KIO    3 ROOM   163   ANG MO KIO AVE 4     01 TO 03   
3  2015-01  ANG MO KIO    3 ROOM   446  ANG MO KIO AVE 10     01 TO 03   
4  2015-01  ANG MO KIO    3 ROOM   557  ANG MO KIO AVE 10     07 TO 09   

   floor_area_sqm      flat_model  lease_commence_date  remaining_lease  \
0            60.0        Improved                 1986               70   
1            68.0  New Generation                 1981               65   
2            69.0  New Generation                 1980               64   
3            68.0  New Generation                 1979               63   
4            68.0  New Generation                 1980               64   

   resale_price  
0      255000.0  
1      275000.0  
2      285000.0  
3      290000.0  
4      290000.0

In [9]:
resale_20152016_df.info()
resale_20152016_df.shape

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 37153 entries, 0 to 37152
Data columns (total 11 columns):
 #   Column               Non-Null Count  Dtype  
---  ------               --------------  -----  
 0   month                37153 non-null  object 
 1   town                 37153 non-null  object 
 2   flat_type            37153 non-null  object 
 3   block                37153 non-null  object 
 4   street_name          37153 non-null  object 
 5   storey_range         37153 non-null  object 
 6   floor_area_sqm       37153 non-null  float64
 7   flat_model           37153 non-null  object 
 8   lease_commence_date  37153 non-null  int64  
 9   remaining_lease      37153 non-null  int64  
 10  resale_price         37153 non-null  float64
dtypes: float64(2), int64(2), object(7)
memory usage: 3.1+ MB


(37153, 11)

In [10]:
resale_2017_df = pd.read_csv('data/2017onwards.csv')
resale_2017_df.head()

month        town flat_type block        street_name storey_range  \
0  2017-01  ANG MO KIO    2 ROOM   406  ANG MO KIO AVE 10     10 TO 12   
1  2017-01  ANG MO KIO    3 ROOM   108   ANG MO KIO AVE 4     01 TO 03   
2  2017-01  ANG MO KIO    3 ROOM   602   ANG MO KIO AVE 5     01 TO 03   
3  2017-01  ANG MO KIO    3 ROOM   465  ANG MO KIO AVE 10     04 TO 06   
4  2017-01  ANG MO KIO    3 ROOM   601   ANG MO KIO AVE 5     01 TO 03   

   floor_area_sqm      flat_model  lease_commence_date     remaining_lease  \
0            44.0        Improved                 1979  61 years 04 months   
1            67.0  New Generation                 1978  60 years 07 months   
2            67.0  New Generation                 1980  62 years 05 months   
3            68.0  New Generation                 1980   62 years 01 month   
4            67.0  New Generation                 1980  62 years 05 months   

   resale_price  
0      232000.0  
1      250000.0  
2      262000.0  
3      265000.0  
4      265000.0

In [11]:
resale_2017_df.info()
resale_2017_df.shape

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 148373 entries, 0 to 148372
Data columns (total 11 columns):
 #   Column               Non-Null Count   Dtype  
---  ------               --------------   -----  
 0   month                148373 non-null  object 
 1   town                 148373 non-null  object 
 2   flat_type            148373 non-null  object 
 3   block                148373 non-null  object 
 4   street_name          148373 non-null  object 
 5   storey_range         148373 non-null  object 
 6   floor_area_sqm       148373 non-null  float64
 7   flat_model           148373 non-null  object 
 8   lease_commence_date  148373 non-null  int64  
 9   remaining_lease      148373 non-null  object 
 10  resale_price         148373 non-null  float64
dtypes: float64(2), int64(1), object(8)
memory usage: 12.5+ MB


(148373, 11)

In [12]:
#all datasets have 10 columns only except resale_20152016_df and resale_2017_df, removed for concat
#bear in mind that remaining_lease may be computed by (99-(month - lease_commence_date)) and can be calculated later
resale_20152016_df.drop(columns=['remaining_lease'], inplace=True)
resale_2017_df.drop(columns=['remaining_lease'], inplace=True)

In [13]:
resale_df=pd.concat([resale_19901999_df, resale_20002012_df, resale_20122014_df, resale_20152016_df, resale_2017_df], ignore_index=True)
resale_df.head()

month        town flat_type block       street_name storey_range  \
0  1990-01  ANG MO KIO    1 ROOM   309  ANG MO KIO AVE 1     10 TO 12   
1  1990-01  ANG MO KIO    1 ROOM   309  ANG MO KIO AVE 1     04 TO 06   
2  1990-01  ANG MO KIO    1 ROOM   309  ANG MO KIO AVE 1     10 TO 12   
3  1990-01  ANG MO KIO    1 ROOM   309  ANG MO KIO AVE 1     07 TO 09   
4  1990-01  ANG MO KIO    3 ROOM   216  ANG MO KIO AVE 1     04 TO 06   

   floor_area_sqm      flat_model  lease_commence_date  resale_price  
0            31.0        IMPROVED                 1977        9000.0  
1            31.0        IMPROVED                 1977        6000.0  
2            31.0        IMPROVED                 1977        8000.0  
3            31.0        IMPROVED                 1977        6000.0  
4            73.0  NEW GENERATION                 1976       47200.0

In [14]:
resale_df.info()
resale_df.shape

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 894576 entries, 0 to 894575
Data columns (total 10 columns):
 #   Column               Non-Null Count   Dtype  
---  ------               --------------   -----  
 0   month                894576 non-null  object 
 1   town                 894576 non-null  object 
 2   flat_type            894576 non-null  object 
 3   block                894576 non-null  object 
 4   street_name          894576 non-null  object 
 5   storey_range         894576 non-null  object 
 6   floor_area_sqm       894576 non-null  float64
 7   flat_model           894576 non-null  object 
 8   lease_commence_date  894576 non-null  int64  
 9   resale_price         894576 non-null  float64
dtypes: float64(2), int64(1), object(7)
memory usage: 68.3+ MB


(894576, 10)

In [15]:
resale_df.columns.to_list()

['month',
 'town',
 'flat_type',
 'block',
 'street_name',
 'storey_range',
 'floor_area_sqm',
 'flat_model',
 'lease_commence_date',
 'resale_price']

In [16]:
# split 'storey_range' to lower integer and higher integer, this can also be used to calculate storey average which may be useful afterwards
# block number to extract number only from 'block'

resale_df['storey_lower'] = resale_df['storey_range'].apply(lambda x: re.findall('\d+',x)[0])
resale_df['storey_upper'] = resale_df['storey_range'].apply(lambda x: re.findall('\d+',x)[1])
resale_df['block_num'] = resale_df['block'].apply(lambda x: re.findall('\A\d+',x)[0])

In [17]:
# convert numeric columns
for x in ['floor_area_sqm','resale_price','storey_lower', 'storey_upper', 'block_num']:
    resale_df[x] = pd.to_numeric(resale_df[x])

In [18]:
# change to time format for date columns
for x in ['month','lease_commence_date']:
    resale_df[x] = pd.to_datetime(resale_df[x].astype(str))

In [19]:
# calculate storey average
resale_df['storey_ave'] = (resale_df['storey_lower'] + resale_df['storey_upper'])/2

In [20]:
# calculating remaining lease for all 
resale_df['remaining_lease'] = resale_df['lease_commence_date'].dt.year + 99 - resale_df['month'].dt.year

In [21]:
# list of features
resale_df.columns.to_list()

['month',
 'town',
 'flat_type',
 'block',
 'street_name',
 'storey_range',
 'floor_area_sqm',
 'flat_model',
 'lease_commence_date',
 'resale_price',
 'storey_lower',
 'storey_upper',
 'block_num',
 'storey_ave',
 'remaining_lease']

In [22]:
categorical_features = ['town', 'flat_type', 'flat_model', 'street_name', 'remaining_lease', 'storey_range', 'block']

In [23]:
# print unique features for each category

for feat in categorical_features:
    print(f'--{feat}--')
    print(resale_df[feat].unique())

--town--
['ANG MO KIO' 'BEDOK' 'BISHAN' 'BUKIT BATOK' 'BUKIT MERAH' 'BUKIT TIMAH'
 'CENTRAL AREA' 'CHOA CHU KANG' 'CLEMENTI' 'GEYLANG' 'HOUGANG'
 'JURONG EAST' 'JURONG WEST' 'KALLANG/WHAMPOA' 'MARINE PARADE'
 'QUEENSTOWN' 'SENGKANG' 'SERANGOON' 'TAMPINES' 'TOA PAYOH' 'WOODLANDS'
 'YISHUN' 'LIM CHU KANG' 'SEMBAWANG' 'BUKIT PANJANG' 'PASIR RIS' 'PUNGGOL']
--flat_type--
['1 ROOM' '3 ROOM' '4 ROOM' '5 ROOM' '2 ROOM' 'EXECUTIVE'
 'MULTI GENERATION' 'MULTI-GENERATION']
--flat_model--
['IMPROVED' 'NEW GENERATION' 'MODEL A' 'STANDARD' 'SIMPLIFIED'
 'MODEL A-MAISONETTE' 'APARTMENT' 'MAISONETTE' 'TERRACE' '2-ROOM'
 'IMPROVED-MAISONETTE' 'MULTI GENERATION' 'PREMIUM APARTMENT' 'Improved'
 'New Generation' 'Model A' 'Standard' 'Apartment' 'Simplified'
 'Model A-Maisonette' 'Maisonette' 'Multi Generation' 'Adjoined flat'
 'Premium Apartment' 'Terrace' 'Improved-Maisonette' 'Premium Maisonette'
 '2-room' 'Model A2' 'DBSS' 'Type S1' 'Type S2' 'Premium Apartment Loft'
 '3Gen']
--street_name--
['ANG MO 

'flat_type' and 'flat_model' has many similar namings and has to be fixed

In [24]:
#function for returning all upper cases and removing non-alphanumeric values
def labeler(feat):
    for value in resale_df[feat].unique():
        if value != ' '.join(re.findall( r'\w+', value.upper())):
                resale_df[feat].replace(value,' '.join(re.findall( r'\w+', value.upper())),inplace=True)

In [25]:
for feat in ['flat_type', 'flat_model']:
    labeler(feat)

In [26]:
resale_df[resale_df.duplicated()]

month         town flat_type block      street_name storey_range  \
673    1990-01-01      GEYLANG    3 ROOM    47       CIRCUIT RD     01 TO 03   
726    1990-01-01      HOUGANG    3 ROOM   308    HOUGANG AVE 5     10 TO 12   
843    1990-01-01  JURONG WEST    3 ROOM   145      HU CHING RD     04 TO 06   
854    1990-01-01  JURONG WEST    3 ROOM   172      BOON LAY DR     10 TO 12   
862    1990-01-01  JURONG WEST    3 ROOM   185     BOON LAY AVE     22 TO 24   
...           ...          ...       ...   ...              ...          ...   
884985 2022-10-01    WOODLANDS    4 ROOM  780C   WOODLANDS CRES     16 TO 18   
886947 2022-11-01    TOA PAYOH    3 ROOM   195     KIM KEAT AVE     01 TO 03   
887082 2022-11-01    WOODLANDS    4 ROOM  574A  WOODLANDS DR 16     04 TO 06   
888060 2022-12-01      HOUGANG    3 ROOM     1    HOUGANG AVE 3     10 TO 12   
888751 2022-12-01    SEMBAWANG    4 ROOM  120C    CANBERRA CRES     10 TO 12   

        floor_area_sqm      flat_model lease_commence_date  resale_price  \
673               56.0        STANDARD          1969-01-01       18000.0   
726               67.0  NEW GENERATION          1983-01-01       47000.0   
843               64.0        IMPROVED          1976-01-01       23400.0   
854               70.0        IMPROVED          1974-01-01       32900.0   
862               59.0        IMPROVED          1975-01-01       22500.0   
...                ...             ...                 ...           ...   
884985            92.0         MODEL A          2015-01-01      520000.0   
886947            66.0        IMPROVED          1973-01-01      290000.0   
887082            93.0         MODEL A          2018-01-01      525000.0   
888060            59.0        IMPROVED          1975-01-01      320000.0   
888751            93.0         MODEL A          2018-01-01      590000.0   

        storey_lower  storey_upper  block_num  storey_ave  remaining_lease  
673                1             3         47         2.0               78  
726               10            12        308        11.0               92  
843                4             6        145         5.0               85  
854               10            12        172        11.0               83  
862               22            24        185        23.0               84  
...              ...           ...        ...         ...              ...  
884985            16            18        780        17.0               92  
886947             1             3        195         2.0               50  
887082             4             6        574         5.0               95  
888060            10            12          1        11.0               52  
888751            10            12        120        11.0               95  

[1941 rows x 15 columns]

The duplicates in this case do not seem like duplicated transactions and will be kept. 

## Getting coordinates of HDB address from OneMap

Similar process from getting coordinates for shopping malls and MRT stations

In [27]:
# address obtained by combining block and street name
resale_df['address'] = resale_df['block'] + " " + resale_df['street_name']
resale_df.head()

month        town flat_type block       street_name storey_range  \
0 1990-01-01  ANG MO KIO    1 ROOM   309  ANG MO KIO AVE 1     10 TO 12   
1 1990-01-01  ANG MO KIO    1 ROOM   309  ANG MO KIO AVE 1     04 TO 06   
2 1990-01-01  ANG MO KIO    1 ROOM   309  ANG MO KIO AVE 1     10 TO 12   
3 1990-01-01  ANG MO KIO    1 ROOM   309  ANG MO KIO AVE 1     07 TO 09   
4 1990-01-01  ANG MO KIO    3 ROOM   216  ANG MO KIO AVE 1     04 TO 06   

   floor_area_sqm      flat_model lease_commence_date  resale_price  \
0            31.0        IMPROVED          1977-01-01        9000.0   
1            31.0        IMPROVED          1977-01-01        6000.0   
2            31.0        IMPROVED          1977-01-01        8000.0   
3            31.0        IMPROVED          1977-01-01        6000.0   
4            73.0  NEW GENERATION          1976-01-01       47200.0   

   storey_lower  storey_upper  block_num  storey_ave  remaining_lease  \
0            10            12        309        11.0               86   
1             4             6        309         5.0               86   
2            10            12        309        11.0               86   
3             7             9        309         8.0               86   
4             4             6        216         5.0               85   

                address  
0  309 ANG MO KIO AVE 1  
1  309 ANG MO KIO AVE 1  
2  309 ANG MO KIO AVE 1  
3  309 ANG MO KIO AVE 1  
4  216 ANG MO KIO AVE 1

In [28]:
addresslist = list(resale_df['address'].astype(str))
addresslist[:5]

['309 ANG MO KIO AVE 1',
 '309 ANG MO KIO AVE 1',
 '309 ANG MO KIO AVE 1',
 '309 ANG MO KIO AVE 1',
 '216 ANG MO KIO AVE 1']

In [29]:
addresslist[-5:]

['335C YISHUN ST 31',
 '334B YISHUN ST 31',
 '715 YISHUN ST 71',
 '820 YISHUN ST 81',
 '356 YISHUN RING RD']

The number of rows within the dataframe is too extensive for address to obtain the coordinates from Onemap API and would take up too much time. There are actually duplicated addresses within and hence in order to shorten time, we will use only the unique addresses before merging back with the original dataframe. 

In [30]:
def unique(list1):
 
    # initialize a null list
    unique_list = []
 
    # traverse for all elements
    for x in list1:
        # check if exists in unique_list or not
        if x not in unique_list:
            unique_list.append(x)
    # print list
    return unique_list

In [31]:
unique_address=unique(addresslist)

In [32]:
len(unique_address)

9718

9718 is much less than initial total number of rows (894576).

In [34]:
def getcoordinates(address, timeout=30):
    try:
        req = requests.get('https://developers.onemap.sg/commonapi/search?searchVal='+address+'&returnGeom=Y&getAddrDetails=Y&pageNum=1', timeout=timeout)
        resultsdict = eval(req.text)
        if len(resultsdict['results'])>0:
            return resultsdict['results'][0]['LATITUDE'], resultsdict['results'][0]['LONGITUDE']
        else:
            return None
    except Timeout:
        print(f"Request timed out after {timeout} seconds.")
        return None

In [35]:
coordinatesdict= {'latitude': [], 'longitude': []}
count = 0
failed_count = 0
for address in unique_address:
    try:
        coordinates = getcoordinates(address)
        if coordinates is not None:
            count = count + 1
            print('Extracting',count,'out of',len(unique_address),'addresses')
            coordinatesdict['latitude'].append(coordinates[0])
            coordinatesdict['longitude'].append(coordinates[1])
        else:
            count = count + 1           
            failed_count = failed_count + 1
            print('Failed to extract',count,'out of',len(unique_address),'addresses')
            coordinatesdict['latitude'].append(None)
            coordinatesdict['longitude'].append(None)
    except:
        count = count + 1           
        failed_count = failed_count + 1
        print('Failed to extract',count,'out of',len(unique_address),'addresses')
        coordinatesdict['latitude'].append(None)
        coordinatesdict['longitude'].append(None)

print('Total Number of Addresses With No Coordinates',failed_count)


Failed to extract 1 out of 9718 addresses
Extracting 2 out of 9718 addresses
Extracting 3 out of 9718 addresses
Extracting 4 out of 9718 addresses
Extracting 5 out of 9718 addresses
Extracting 6 out of 9718 addresses
Extracting 7 out of 9718 addresses
Extracting 8 out of 9718 addresses
Extracting 9 out of 9718 addresses
Failed to extract 10 out of 9718 addresses
Extracting 11 out of 9718 addresses
Failed to extract 12 out of 9718 addresses
Extracting 13 out of 9718 addresses
Extracting 14 out of 9718 addresses
Extracting 15 out of 9718 addresses
Extracting 16 out of 9718 addresses
Extracting 17 out of 9718 addresses
Extracting 18 out of 9718 addresses
Extracting 19 out of 9718 addresses
Extracting 20 out of 9718 addresses
Extracting 21 out of 9718 addresses
Extracting 22 out of 9718 addresses
Extracting 23 out of 9718 addresses
Extracting 24 out of 9718 addresses
Extracting 25 out of 9718 addresses
Extracting 26 out of 9718 addresses
Extracting 27 out of 9718 addresses
Extracting 28 ou

In [36]:
# matching address back with coordinates
coordinatesdict['address'] = unique_address

In [37]:
coordinates_df=pd.DataFrame.from_dict(coordinatesdict)
coordinates_df.head()

latitude         longitude               address
0              None              None  309 ANG MO KIO AVE 1
1  1.36619678831054  103.841505011903  216 ANG MO KIO AVE 1
2    1.369196965617  103.841666636086  211 ANG MO KIO AVE 3
3  1.36845752328237  103.844515336938  202 ANG MO KIO AVE 3
4  1.36682360708102   103.83649123895  235 ANG MO KIO AVE 3

In [38]:
coordinates_df.to_csv('data/coordinates.csv', index=False)

In [39]:
# merging to new dataframe on address, keeping all rows in original dataframe
resale=pd.merge(resale_df,coordinates_df, how='left' ,on = 'address')

In [40]:
resale.shape

(894576, 18)

In [41]:
resale.head()

month        town flat_type block       street_name storey_range  \
0 1990-01-01  ANG MO KIO    1 ROOM   309  ANG MO KIO AVE 1     10 TO 12   
1 1990-01-01  ANG MO KIO    1 ROOM   309  ANG MO KIO AVE 1     04 TO 06   
2 1990-01-01  ANG MO KIO    1 ROOM   309  ANG MO KIO AVE 1     10 TO 12   
3 1990-01-01  ANG MO KIO    1 ROOM   309  ANG MO KIO AVE 1     07 TO 09   
4 1990-01-01  ANG MO KIO    3 ROOM   216  ANG MO KIO AVE 1     04 TO 06   

   floor_area_sqm      flat_model lease_commence_date  resale_price  \
0            31.0        IMPROVED          1977-01-01        9000.0   
1            31.0        IMPROVED          1977-01-01        6000.0   
2            31.0        IMPROVED          1977-01-01        8000.0   
3            31.0        IMPROVED          1977-01-01        6000.0   
4            73.0  NEW GENERATION          1976-01-01       47200.0   

   storey_lower  storey_upper  block_num  storey_ave  remaining_lease  \
0            10            12        309        11.0               86   
1             4             6        309         5.0               86   
2            10            12        309        11.0               86   
3             7             9        309         8.0               86   
4             4             6        216         5.0               85   

                address          latitude         longitude  
0  309 ANG MO KIO AVE 1              None              None  
1  309 ANG MO KIO AVE 1              None              None  
2  309 ANG MO KIO AVE 1              None              None  
3  309 ANG MO KIO AVE 1              None              None  
4  216 ANG MO KIO AVE 1  1.36619678831054  103.841505011903

In [42]:
resale['latitude'].isna().sum()

11625

In [43]:
#resale flats with no coordinates account for about 1.28% of total data set, these can be dropped
resale=resale.loc[resale['latitude'].notna(), :]

In [44]:
resale.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 882951 entries, 4 to 894575
Data columns (total 18 columns):
 #   Column               Non-Null Count   Dtype         
---  ------               --------------   -----         
 0   month                882951 non-null  datetime64[ns]
 1   town                 882951 non-null  object        
 2   flat_type            882951 non-null  object        
 3   block                882951 non-null  object        
 4   street_name          882951 non-null  object        
 5   storey_range         882951 non-null  object        
 6   floor_area_sqm       882951 non-null  float64       
 7   flat_model           882951 non-null  object        
 8   lease_commence_date  882951 non-null  datetime64[ns]
 9   resale_price         882951 non-null  float64       
 10  storey_lower         882951 non-null  int64         
 11  storey_upper         882951 non-null  int64         
 12  block_num            882951 non-null  int64         
 13  storey_ave    

In [45]:
resale.to_csv('data/resale.csv', index=False)

## Calculating distance from HDB address to Malls and MRT Stations

In [46]:
#pip install geopy 

In [47]:
import geopy.distance

In [48]:
#filtering only required columns and keeping only unique addresses
resale_coordinates_df=resale[['address','latitude','longitude']]
resale_coordinates_df=resale_coordinates_df.drop_duplicates(subset=['address'],ignore_index=True)

In [49]:
print(resale_coordinates_df.shape)
resale_coordinates_df.head()

(9588, 3)


address          latitude         longitude
0  216 ANG MO KIO AVE 1  1.36619678831054  103.841505011903
1  211 ANG MO KIO AVE 3    1.369196965617  103.841666636086
2  202 ANG MO KIO AVE 3  1.36845752328237  103.844515336938
3  235 ANG MO KIO AVE 3  1.36682360708102   103.83649123895
4  232 ANG MO KIO AVE 3  1.36834606813391  103.837196046409

In [50]:
# geopy distance requires the coordinates to be placed in a tuple
resale_coordinates_df['lat_long'] = resale_coordinates_df['latitude'] +' '+ resale_coordinates_df['longitude']
# convert lat_long column to tuples
resale_coordinates_df['lat_long'] = resale_coordinates_df['lat_long'].apply(lambda x: tuple(x.split(' ')))

In [51]:
resale_coordinates_df.head()

address          latitude         longitude  \
0  216 ANG MO KIO AVE 1  1.36619678831054  103.841505011903   
1  211 ANG MO KIO AVE 3    1.369196965617  103.841666636086   
2  202 ANG MO KIO AVE 3  1.36845752328237  103.844515336938   
3  235 ANG MO KIO AVE 3  1.36682360708102   103.83649123895   
4  232 ANG MO KIO AVE 3  1.36834606813391  103.837196046409   

                               lat_long  
0  (1.36619678831054, 103.841505011903)  
1    (1.369196965617, 103.841666636086)  
2  (1.36845752328237, 103.844515336938)  
3   (1.36682360708102, 103.83649123895)  
4  (1.36834606813391, 103.837196046409)

### Load MRT coordinates

In [52]:
mrt_coordinates_df = pd.read_csv('data/mrt_coordinates.csv')
mrt_coordinates_df.head()

latitude   longitude                        mrt
0  1.333295  103.742154    Jurong East MRT Station
1  1.349033  103.749566    Bukit Batok MRT Station
2  1.358612  103.751791   Bukit Gombak MRT Station
3  1.385363  103.744371  Choa Chu Kang MRT Station
4  1.397476  103.747418        Yew Tee MRT Station

In [53]:
# importing from csv reads lat and long as int, required to be converted to type string in order to achieve lat_long tuple later
mrt_coordinates_df=mrt_coordinates_df.astype(str)

In [54]:
mrt_coordinates_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 120 entries, 0 to 119
Data columns (total 3 columns):
 #   Column     Non-Null Count  Dtype 
---  ------     --------------  ----- 
 0   latitude   120 non-null    object
 1   longitude  120 non-null    object
 2   mrt        120 non-null    object
dtypes: object(3)
memory usage: 2.9+ KB


In [55]:
# Do the same for the MRT coordinates
mrt_coordinates_df['lat_long'] = mrt_coordinates_df['latitude'] +' '+ mrt_coordinates_df['longitude']
# convert lat_long column to tuples
mrt_coordinates_df['lat_long'] = mrt_coordinates_df['lat_long'].apply(lambda x: tuple(x.split(' ')))

In [56]:
mrt_coordinates_df.head()

latitude         longitude                        mrt  \
0  1.33329506563598  103.742153884191    Jurong East MRT Station   
1  1.34903331201636  103.749566478309    Bukit Batok MRT Station   
2  1.35861159094192  103.751790910733   Bukit Gombak MRT Station   
3  1.38536316540225  103.744370779756  Choa Chu Kang MRT Station   
4  1.39747594171731  103.747418249132        Yew Tee MRT Station   

                               lat_long  
0  (1.33329506563598, 103.742153884191)  
1  (1.34903331201636, 103.749566478309)  
2  (1.35861159094192, 103.751790910733)  
3  (1.38536316540225, 103.744370779756)  
4  (1.39747594171731, 103.747418249132)

In [57]:
mrt_coordinates_list=mrt_coordinates_df['lat_long'].tolist()

Calculating first mrt coordinate with first resale coordinate

This can then be used to verify for loop is working correctly later

In [58]:
mrt_coordinates_list[0]

('1.33329506563598', '103.742153884191')

In [59]:
resale_coordinates_df['lat_long'][0]

('1.36619678831054', '103.841505011903')

In [60]:
# calculating distance in KM
distance_geopy = geopy.distance.distance(resale_coordinates_df['lat_long'][0], mrt_coordinates_list[0]).km
print('distance using geopy: ', distance_geopy)

distance using geopy:  11.63983355896618


Using for loop to iterate each HDB address coordinate with all MRT station coordinates

In [61]:
%%time
distance = []
for address_point in resale_coordinates_df['lat_long']:
    address_distances = []
    for point in mrt_coordinates_list:
        distance_geopy = geopy.distance.distance(address_point, point).km
        address_distances.append(distance_geopy)
    distance.append(address_distances)

CPU times: user 1min 31s, sys: 331 ms, total: 1min 32s
Wall time: 1min 32s


In [62]:
# nested list of mrt distance to each HDB resale address
# double check first value with above
distance

[[11.63983355896618,
  10.40622201522667,
  10.019291303766307,
  11.01562960712471,
  11.027119243450265,
  10.973478810815395,
  10.492672290129889,
  9.757523072495095,
  9.380475705570905,
  9.467705756415556,
  8.601854160091667,
  7.0307655350083085,
  5.7389160665187955,
  1.7557403234973423,
  0.9542049055736572,
  1.8519088452754289,
  2.905215644760872,
  3.7762810792258352,
  5.0660512234422335,
  5.970407233546448,
  7.319915886456819,
  7.295461247988989,
  7.486844173874861,
  8.187512580091834,
  9.163539795336211,
  10.032618197302044,
  10.778391265475577,
  12.018423536630488,
  11.027149513359218,
  12.707194146717878,
  12.439721924463333,
  13.833895430155073,
  9.388805412454735,
  8.57437944289127,
  7.823186283661287,
  7.176927974997169,
  6.90312627535985,
  6.920991230279423,
  7.438132215823227,
  9.919169288412375,
  9.562549129493886,
  8.993574853393309,
  8.90316024067371,
  8.849135986737531,
  8.532316547028413,
  8.663452996785757,
  9.255074698142426

In [63]:
# we only require the closest distance to mrt as a parameter for buyers consideration
minimum_distances_to_mrt = [min(distances) for distances in distance]
minimum_distances_to_mrt

[0.9542049055736572,
 0.867154179787593,
 0.560137387874075,
 1.471208668687082,
 1.3695394916660488,
 0.7024419364071703,
 1.0813686015896269,
 1.050997312872973,
 0.44052929113036876,
 1.3154004273690802,
 1.2777693790011093,
 0.4247091735783257,
 0.31640917772277105,
 1.3658695708252862,
 1.344298211112925,
 0.12134011355618973,
 0.21579556650893897,
 0.2589642152863611,
 0.6703728451114389,
 0.8247192416717712,
 0.8499458000329685,
 0.6755808815743309,
 0.6818742701156446,
 0.6917742099415326,
 1.0711093400206844,
 1.0385925527205038,
 0.9938361736155948,
 0.8077863994628656,
 0.7116141000299437,
 0.6905847637825199,
 0.6439347953613052,
 0.7516667780796726,
 0.7571018216502299,
 0.7498038579593088,
 0.6772665070901055,
 0.5629255775808281,
 0.5651986824060247,
 0.47647289358484635,
 0.17593191740578673,
 0.24284526435510512,
 0.9358464535465787,
 1.0417587774281933,
 1.204819361313711,
 0.731758712224685,
 0.45561720548805784,
 0.932964388491256,
 0.8924727459023203,
 1.1081655245

In [64]:
# double check that this corresponds to unique HDB addresses
len(minimum_distances_to_mrt)

9588

In [65]:
print(f'Minimum distance to MRT ranges from {min(minimum_distances_to_mrt)} to {max(minimum_distances_to_mrt)}')

Minimum distance to MRT ranges from 0.036079525074360914 to 5.471182805936466


### Load Shopping Malls coordinates
Repeat similar steps for shopping mall coordinates

In [66]:
mall_coordinates_df = pd.read_csv('data/malls_coordinates.csv')
mall_coordinates_df.head()

latitude   longitude                           malls
0  1.274683  103.843488                          100 AM
1  1.301014  103.838361                    313@Somerset
2  1.309711  103.864326                          Aperia
3  1.325596  103.842572  Balestier Hill Shopping Centre
4  1.298141  103.855635                      Bugis Cube

In [67]:
# importing from csv reads lat and long as int, required to be converted to type string in order to achieve lat_long tuple later
mall_coordinates_df=mall_coordinates_df.astype(str)

In [68]:
mall_coordinates_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 166 entries, 0 to 165
Data columns (total 3 columns):
 #   Column     Non-Null Count  Dtype 
---  ------     --------------  ----- 
 0   latitude   166 non-null    object
 1   longitude  166 non-null    object
 2   malls      166 non-null    object
dtypes: object(3)
memory usage: 4.0+ KB


In [69]:
# Do the same for the Shopping Mall coordinates
mall_coordinates_df['lat_long'] = mall_coordinates_df['latitude'] +' '+ mall_coordinates_df['longitude']
# convert lat_long column to tuples
mall_coordinates_df['lat_long'] = mall_coordinates_df['lat_long'].apply(lambda x: tuple(x.split(' ')))

In [70]:
mall_coordinates_df.head()

latitude         longitude                           malls  \
0  1.27468281482263  103.843488359469                          100 AM   
1  1.30101436404056  103.838360664485                    313@Somerset   
2   1.3097112065077  103.864326436447                          Aperia   
3  1.32559594839311  103.842571612968  Balestier Hill Shopping Centre   
4   1.2981408343975  103.855635339249                      Bugis Cube   

                               lat_long  
0  (1.27468281482263, 103.843488359469)  
1  (1.30101436404056, 103.838360664485)  
2   (1.3097112065077, 103.864326436447)  
3  (1.32559594839311, 103.842571612968)  
4   (1.2981408343975, 103.855635339249)

In [71]:
mall_coordinates_list=mall_coordinates_df['lat_long'].tolist()

In [72]:
%%time
distance = []
for address_point in resale_coordinates_df['lat_long']:
    address_distances = []
    for point in mall_coordinates_list:
        distance_geopy = geopy.distance.distance(address_point, point).km
        address_distances.append(distance_geopy)
    distance.append(address_distances)

CPU times: user 2min 7s, sys: 525 ms, total: 2min 8s
Wall time: 2min 8s


In [73]:
# we only require the closest distance to mrt as a parameter for buyers consideration
minimum_distances_to_mall = [min(distances) for distances in distance]
minimum_distances_to_mall

[0.804708264621686,
 0.5647891715648522,
 0.41656164252620237,
 1.1948477691187267,
 1.051974475082576,
 0.6148457998488087,
 0.9263366101476588,
 0.8836993554395243,
 0.4199514140359653,
 1.0875366117704526,
 0.9529629794994505,
 0.35641361975953306,
 0.35455899256705853,
 1.1673104558513716,
 0.9632693105470251,
 0.13488967486015307,
 0.24759658363327605,
 0.28579484247644377,
 0.37312015131497545,
 0.48831021231933525,
 0.4839322973925853,
 0.2939724264737669,
 0.2738381571800467,
 0.25850888718078924,
 1.1299729802538911,
 1.1003034380662777,
 1.047526466298212,
 0.8939015923824654,
 0.790566259479453,
 0.7736395639551659,
 0.7330337939432102,
 0.8425241658998469,
 0.8514385624959093,
 0.8482715621111093,
 0.7843353397504309,
 0.6650380523852367,
 0.6697436191904069,
 0.5781153811747268,
 0.2734489412084285,
 0.35047556589242534,
 0.9045617918134812,
 0.9586162527916416,
 0.8366917227099722,
 0.8406001295805302,
 0.5631330214540597,
 0.8937956343800417,
 0.9196568962674456,
 0.8271

In [74]:
print(f'Minimum distance to mall ranges from {min(minimum_distances_to_mall)} to {max(minimum_distances_to_mall)}')

Minimum distance to mall ranges from 0.0 to 5.3987141111572505


### Finalising data frame

In [75]:
temp_df=resale_coordinates_df[['address']]
temp_df['min_distance_to_mrt']= minimum_distances_to_mrt
temp_df['min_distance_to_mall']= minimum_distances_to_mall

/var/folders/mx/5sy10vfd4s7ct44z5lb0s3mr0000gn/T/ipykernel_11867/3902632128.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  temp_df['min_distance_to_mrt']= minimum_distances_to_mrt
/var/folders/mx/5sy10vfd4s7ct44z5lb0s3mr0000gn/T/ipykernel_11867/3902632128.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  temp_df['min_distance_to_mall']= minimum_distances_to_mall


In [76]:
temp_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9588 entries, 0 to 9587
Data columns (total 3 columns):
 #   Column                Non-Null Count  Dtype  
---  ------                --------------  -----  
 0   address               9588 non-null   object 
 1   min_distance_to_mrt   9588 non-null   float64
 2   min_distance_to_mall  9588 non-null   float64
dtypes: float64(2), object(1)
memory usage: 224.8+ KB


In [77]:
print(temp_df.shape)
temp_df.head()

(9588, 3)


address  min_distance_to_mrt  min_distance_to_mall
0  216 ANG MO KIO AVE 1             0.954205              0.804708
1  211 ANG MO KIO AVE 3             0.867154              0.564789
2  202 ANG MO KIO AVE 3             0.560137              0.416562
3  235 ANG MO KIO AVE 3             1.471209              1.194848
4  232 ANG MO KIO AVE 3             1.369539              1.051974

In [78]:
resale.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 882951 entries, 4 to 894575
Data columns (total 18 columns):
 #   Column               Non-Null Count   Dtype         
---  ------               --------------   -----         
 0   month                882951 non-null  datetime64[ns]
 1   town                 882951 non-null  object        
 2   flat_type            882951 non-null  object        
 3   block                882951 non-null  object        
 4   street_name          882951 non-null  object        
 5   storey_range         882951 non-null  object        
 6   floor_area_sqm       882951 non-null  float64       
 7   flat_model           882951 non-null  object        
 8   lease_commence_date  882951 non-null  datetime64[ns]
 9   resale_price         882951 non-null  float64       
 10  storey_lower         882951 non-null  int64         
 11  storey_upper         882951 non-null  int64         
 12  block_num            882951 non-null  int64         
 13  storey_ave    

In [79]:
final_resale=pd.merge(resale,temp_df, how='left' ,on = 'address')

In [80]:
final_resale.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 882951 entries, 0 to 882950
Data columns (total 20 columns):
 #   Column                Non-Null Count   Dtype         
---  ------                --------------   -----         
 0   month                 882951 non-null  datetime64[ns]
 1   town                  882951 non-null  object        
 2   flat_type             882951 non-null  object        
 3   block                 882951 non-null  object        
 4   street_name           882951 non-null  object        
 5   storey_range          882951 non-null  object        
 6   floor_area_sqm        882951 non-null  float64       
 7   flat_model            882951 non-null  object        
 8   lease_commence_date   882951 non-null  datetime64[ns]
 9   resale_price          882951 non-null  float64       
 10  storey_lower          882951 non-null  int64         
 11  storey_upper          882951 non-null  int64         
 12  block_num             882951 non-null  int64         
 13 

In [81]:
final_resale.head()

month        town flat_type block       street_name storey_range  \
0 1990-01-01  ANG MO KIO    3 ROOM   216  ANG MO KIO AVE 1     04 TO 06   
1 1990-01-01  ANG MO KIO    3 ROOM   211  ANG MO KIO AVE 3     01 TO 03   
2 1990-01-01  ANG MO KIO    3 ROOM   202  ANG MO KIO AVE 3     07 TO 09   
3 1990-01-01  ANG MO KIO    3 ROOM   235  ANG MO KIO AVE 3     10 TO 12   
4 1990-01-01  ANG MO KIO    3 ROOM   235  ANG MO KIO AVE 3     04 TO 06   

   floor_area_sqm      flat_model lease_commence_date  resale_price  \
0            73.0  NEW GENERATION          1976-01-01       47200.0   
1            67.0  NEW GENERATION          1977-01-01       46000.0   
2            67.0  NEW GENERATION          1977-01-01       42000.0   
3            67.0  NEW GENERATION          1977-01-01       38000.0   
4            67.0  NEW GENERATION          1977-01-01       40000.0   

   storey_lower  storey_upper  block_num  storey_ave  remaining_lease  \
0             4             6        216         5.0               85   
1             1             3        211         2.0               86   
2             7             9        202         8.0               86   
3            10            12        235        11.0               86   
4             4             6        235         5.0               86   

                address          latitude         longitude  \
0  216 ANG MO KIO AVE 1  1.36619678831054  103.841505011903   
1  211 ANG MO KIO AVE 3    1.369196965617  103.841666636086   
2  202 ANG MO KIO AVE 3  1.36845752328237  103.844515336938   
3  235 ANG MO KIO AVE 3  1.36682360708102   103.83649123895   
4  235 ANG MO KIO AVE 3  1.36682360708102   103.83649123895   

   min_distance_to_mrt  min_distance_to_mall  
0             0.954205              0.804708  
1             0.867154              0.564789  
2             0.560137              0.416562  
3             1.471209              1.194848  
4             1.471209              1.194848

In [82]:
final_resale.to_csv('data/final_resale.csv', index=False)